# LinkedIn Hiring Rate Analysis: South Asian Labor Market Dynamics (2018-2024)
The analysis of LinkedIn Hiring Rate (LHR) data reveals distinct patterns across South Asian economies, with notable variations in labor market recovery. The countries analysed are Sri Lanka, Nepal, India and Bangladesh. 

In [26]:
import pandas as pd
import numpy as np
from bokeh.plotting import figure, output_notebook, show
from bokeh.models import ColumnDataSource, HoverTool, Tabs, TabPanel, Toggle, CustomJS
from bokeh.palettes import Category20
from bokeh.layouts import column

In [27]:
def clean_linkedin_data(excel_file):
    """Clean and prepare LinkedIn data from Excel file."""
    try:
        data_corrected = pd.read_excel(excel_file, sheet_name="3A - LHR by Ctry", header=3)

        data_cleaned = data_corrected.rename(columns={
            'Unnamed: 1': 'Month',
            'Unnamed: 2': 'Country',
            'Unnamed: 3': 'LHR (YOY)'
        })

        data_cleaned = data_cleaned.dropna(subset=['Month', 'Country', 'LHR (YOY)'])
        data_cleaned = data_cleaned.iloc[1:]
        data_cleaned = data_cleaned.drop(columns=['Unnamed: 0'])

        # Clean up whitespace and standardize country names
        data_cleaned["Country"] = data_cleaned["Country"].str.strip()
        data_cleaned["Country"] = data_cleaned["Country"].replace({
            "Turkey": "Turkiye",
            "Türkiye": "Turkiye"
        })

        return data_cleaned

    except Exception as e:
        print(f"Error during data cleaning: {str(e)}")
        return None



In [35]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.models import (
    ColumnDataSource, HoverTool, Tabs, TabPanel, Toggle, CustomJS, Button
)
from bokeh.layouts import column
from bokeh.palettes import Category20
import pandas as pd

def create_country_plots(excel_file):
    """Create interactive plots showing LinkedIn Hiring Rate by Country with 2022+ filter toggle and download button."""
    output_notebook()
    
    country_map = {
        'BD': 'Bangladesh',
        'IN': 'India',
        'LK': 'Sri Lanka',
        'NP': 'Nepal', 
        'ZA': 'South Africa', 
        'TR': 'Turkiye',
        'ID': 'Indonesia', 
        'US': 'United States'
    }
    
    try:
        df = clean_linkedin_data(excel_file)
        
        if df is None:
            print("Data cleaning failed. Please check your Excel file.")
            return
        
        # Compute global y-axis range for all countries
        global_min = df['LHR (YOY)'].min()
        global_max = df['LHR (YOY)'].max()

        tabs = []

        for idx, (country_code, country_name) in enumerate(country_map.items()):
            country_data = df[df['Country'] == country_name].copy()
            if country_data.empty:
                print(f"No data available for {country_name}.")
                continue

            # Keep datetime format for plotting
            country_data['Month'] = pd.to_datetime(country_data['Month'])
            country_data = country_data.sort_values('Month')

            # Add string version of Month for download
            country_data['Month_str'] = country_data['Month'].dt.strftime('%Y-%m')

            # Prepare sources
            full_data = country_data
            filtered_data = full_data[full_data['Month'] >= '2022-01-01']

            source = ColumnDataSource(full_data)
            source_filtered = ColumnDataSource(filtered_data)
            # Download source: string Month only
            source_download = ColumnDataSource(
                full_data[['Country', 'Month_str', 'LHR (YOY)']].rename(columns={'Month_str': 'Month'})
            )

            # Create plot
            p = figure(
                title=f"LinkedIn Hiring Rate in {country_name}",
                x_axis_type='datetime',
                width=800,
                height=500,
                background_fill_color="#f8f9fa",
                y_range=(global_min, global_max)
            )

            p.line(
                x='Month',
                y='LHR (YOY)',
                source=source,
                line_width=3,
                color=Category20[20][idx % 20]
            )

            hover = HoverTool(tooltips=[
                ("Month", "@Month{%b %Y}"),
                ("LHR (YOY)", "@{LHR (YOY)}{0.00}%")
            ], formatters={"@Month": "datetime"}, mode='vline')
            p.add_tools(hover)

            p.xaxis.axis_label = 'Month'
            p.yaxis.axis_label = 'LinkedIn Hiring Rate (YOY %)'
            p.xaxis.axis_label_text_font_size = '12pt'
            p.yaxis.axis_label_text_font_size = '12pt'
            p.xaxis.major_label_text_font_size = '10pt'
            p.yaxis.major_label_text_font_size = '10pt'
            p.title.text_font_size = '14pt'
            p.grid.grid_line_color = "gray"
            p.grid.grid_line_alpha = 0.3

            # Toggle button
            toggle = Toggle(label="Show only from 2022", button_type="success", active=False)

            callback = CustomJS(args=dict(
                toggle=toggle,
                source=source,
                full=source.data,
                filtered=source_filtered.data
            ), code="""
                source.data = toggle.active ? filtered : full;
                source.change.emit();
                toggle.label = toggle.active ? "Show full range" : "Show only from 2022";
                toggle.button_type = toggle.active ? "warning" : "success";
            """)
            toggle.js_on_change("active", callback)

            # Download button
            download_button = Button(label="Download CSV", button_type="primary")

            download_js = CustomJS(args=dict(source=source_download, name=country_name), code="""
                const data = source.data;
                const cols = ["Country", "Month", "LHR (YOY)"];
                const nrows = data[cols[0]].length;
                let csv = cols.join(",") + "\\n";
                for (let i = 0; i < nrows; i++) {
                    let row = cols.map(col => data[col][i]);
                    csv += row.join(",") + "\\n";
                }
                const blob = new Blob([csv], { type: 'text/csv;charset=utf-8;' });
                const link = document.createElement("a");
                link.href = URL.createObjectURL(blob);
                const filename = "linkedin_HR_" + name.replace(/ /g, "_") + ".csv";
                link.download = filename;
                link.click();
            """)
            download_button.js_on_click(download_js)

            # Combine all widgets
            layout = column(toggle, download_button, p)
            tab = TabPanel(child=layout, title=country_name)
            tabs.append(tab)

        if tabs:
            show(Tabs(tabs=tabs))
        else:
            print("No data available for any of the specified countries.")
    
    except Exception as e:
        print(f"An error occurred: {str(e)}")
        print("Please check your Excel file structure and column names.")




In [36]:
from bokeh.io import output_notebook, show
output_notebook()
file_path = '../../data/LinkedIn/LinkedIn_LHR by Industry_9Dec2024.xlsx'

create_country_plots(file_path)

Loading BokehJS ...

Loading BokehJS ...

### Insights

**COVID-19 Impact (2020)**
- All markets experienced significant contraction. Every country had uniform negative growth rates (~-0.5%) with Nepal seeing the biggest dip at -0.66% and India being at -0.47%. However, it is important to keep in mind that the coverage in India is better than the rest of the countries in this region. 
- Recovery patterns diverged significantly post-2020

**Post-COVID Recovery Surge (2021)**
- The **April 2021 jump** in LHR is driven by YOY calculations (see the [methodology document](#) for details).  
  - This spike reflects an **extraordinary increase in labor market churn** compared to April 2020, when hiring was at historic lows due to the COVID-19 pandemic.  
  - The surge is not necessarily due to an unusual increase in hiring activity but rather a **rebound effect** from the suppressed hiring levels of the previous year.
- All four countries experienced a significant hiring surge in mid-2021, with peak YoY growth rates of: Sri Lanka: ~3% (highest regional peak), Nepal: ~2.7%, Bangladesh: ~2.3%, India: ~1.5%
- This synchronized peak suggests a regional "catch-up" effect following COVID-19 disruptions

**Market Stabilization Patterns (2022-2024)**
1. **India**: Shows the most stable recovery trajectory with a gradual decline from 2021 peak and recent stabilization around 0% YoY growth
2. **Bangladesh**: Exhibits moderate volatility. More pronounced fluctuations post-recovery. Recent trend hovering between -0.5% to 0% while every other country in this region is averaging around 0%. 
3. **Sri Lanka**: Demonstrates high volatility. Sharp decline from peak post COVID. This could also be because the peak was unnaturally high. 
4. **Nepal**: Shows similar patterns to Bangladesh. Recent stabilization near 0% growth. 